# Homework 6

Due Friday, May 26, 7:59am

# Integer Programming: Fantasy Football

In this homework, you will use integer programming to select an entry for a fantasy football competition. In these competitions, each participant selects players to compose a fantasy team, and the goal is to choose a set that maximizes the number of points these players will score in real-life games.

Each fantasy entry consists of 9 players. The selection of players is subject to two main types of constraints. The first type restricts the choice of players by position. Namely, a feasible entry contains the following number of players per position (you will find this information for each player in the column 'Position'): 

*   1 QB player
*   2 RB player
*   3 WR player
*   1 TE player
*   1 DST player
*   1 FLEX player

In the accompanying csv file, you will see the projections from Saber Sim (https://www.sabersim.com/) which are posted prior to the start of the games.  This file gives you all of the information you need to build a lineup. 

Each player has a fantasy salary (you will find this information for each player in the column 'Salary'), and there is a budget restriction of \$50,000 over the entry. In other words, the sum of the salaries of the players selected in your entry cannot be larger than \$50,000. The player positions are listed in column 'Pos'.

Your goal is to identify a feasible entry that maximizes the expected number of points (you will find this information for each player in the column 'SS Proj'). The extraction and basic filtering of the data have been provided to you (so please don't change that!!!). As output, **you should print the number of fantasy points scored by your entry and a dataframe containing only the entries for the 9 players you selected.**

After finding the best expected value team, your goal is to incorporate what is commonly referred to as stacking constraints:

*   For the QB selected, pick at least 2 players that are TE or WR from the QB's team
*   Do not pick the opposing DST of any player selected

Incorporate these constraints, even if the solution without these constraints satisfies the stacking constraints.

**Curiosity**:  Prof. David Bergman, from the OPIM Department, made a lot of money playing this game: 
https://today.uconn.edu/2021/01/business-professor-wins-2-5-million-fantasy-football-jackpot-using-concepts-teaches-students/

The data we provided was from the day of the competition that David Bergman won. His winning lineup consisted of the following players:


*   QB: Kyle Murray
*   RB: Alvin Kamara
*   RB: Chase Edmonds
*   WR: DeAndre Hopkins
*   WR: Calvin Ridley
*   WR: Emmanuel Sanders
*   TE: Durham Smythe
*   DST: Cowboys
*   FLEX: Tony Pollard

In the csv included, you will also see the actual points fantasy points that each player scored in the column titled 'Actual' (which is of course not available at the time that the lineup construction occurs).  David Bergman's lineup scored 208.24 points.  How many points did your lineup score?  Maybe David did something more than just maximize expected value?






In [24]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [25]:
import sys
import os
 
if 'google.colab' in sys.modules:
    !pip install idaes-pse --pre
    !idaes get-extensions --to ./bin
    os.environ['PATH'] += ':bin'

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from pyomo.environ import *

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Getting files...
Done
---------------------------------------------------
IDAES Extensions Build Versions
Solvers:  vno version file found
Library:  vno version file found


In [26]:
#Read the dataset
players_df = pd.read_csv('/content/drive/MyDrive/BDM /NFL_2020-12-20_DK_12_20-100PM-11-games-Main - NFL_2020-12-20_DK_12_20-100PM-11-games-Main.csv')
players_df.head()

DFS ID             Name      Pos Team  Opp Status  Salary  Actual  \
0  15958102     Kyler Murray       QB  ARI  PHI    NaN    7000   38.14   
1  15958099  Patrick Mahomes       QB   KC   NO    NaN    7900   26.86   
2  15958163     Alvin Kamara  RB,FLEX   NO   KC    NaN    7400   18.40   
3  15958100    Lamar Jackson       QB  BAL  JAX    NaN    7500   30.22   
4  15958159    Derrick Henry  RB,FLEX  TEN  DET    NaN    9500   28.20   

   SS Proj  My Proj  ...  Completions  Pass Yds  Pass TD  Pass Int     Rec  \
0  26.8949    26.89  ...      23.3502   248.033   2.0134    0.3942  0.0000   
1  25.6601    25.66  ...      27.2068   306.225   2.5134    0.5502  0.0000   
2  25.1607    25.16  ...       0.0000     0.000   0.0000    0.0000  8.0298   
3  24.5062    24.51  ...      16.7272   180.542   1.4810    0.3006  0.0000   
4  23.6679    23.67  ...       0.0000     0.000   0.0000    0.0000  1.0300   

   Rec Yds  Rec TD  Rush Att  Rush Yds  Rush TD  
0   0.0000  0.0000    8.2610   49.8164   0.6456  
1   0.0000  0.0000    2.3422   14.7851   0.1790  
2  54.9403  0.2492   14.2428   63.5629   0.5402  
3   0.0000  0.0000   10.7524   70.3696   0.7088  
4   7.6075  0.0190   26.9694  124.8280   1.2118  

[5 rows x 50 columns]

In [27]:
players_df.isna().sum()


DFS ID                   0
Name                     0
Pos                      0
Team                     0
Opp                      0
Status                 305
Salary                   0
Actual                 233
SS Proj                195
My Proj                  0
Value                    0
SS Own                   0
My Own                   0
Min Exp                449
Max Exp                449
dk_points              195
dk_25_percentile       195
dk_50_percentile       195
dk_75_percentile       195
dk_85_percentile       195
dk_95_percentile       195
dk_99_percentile       195
fd_points              195
fd_25_percentile       195
fd_50_percentile       195
fd_75_percentile       195
fd_85_percentile       195
fd_95_percentile       195
fd_99_percentile       195
yahoo_points           195
yahoo_25_percentile    195
yahoo_50_percentile    195
yahoo_75_percentile    195
yahoo_85_percentile    195
yahoo_95_percentile    195
yahoo_99_percentile    195
dk_std                 195
f

In [28]:
players_df['SS Proj'].fillna(0,inplace=True)
players_df['Actual'].fillna(0,inplace=True)

## Part A: Salary, Position & Players Constraint

In [29]:
n_players = len(players_df)
n_positions = 9
pos_by_index = ['QB','RB','RB','WR','WR','WR','TE','DST','FLEX']

print(n_players)

449


In [30]:
model = ConcreteModel()
model.x = Var(range(n_players), range(n_positions), within=Binary)

## objective function
objective_expr = sum(model.x[p, q] * players_df.loc[p, 'SS Proj'] for p in range(n_players) for q in range(n_positions) if players_df.loc[p, 'SS Proj'] != 0)
model.total_time = Objective(expr=objective_expr, sense=maximize)

# Salary Constraint
model.salary_constraint = ConstraintList()
total_salary = sum(model.x[p, q] * players_df.loc[p, 'Salary'] for p in range(n_players) for q in range(n_positions) if players_df.loc[p, 'SS Proj'] != 0)
model.salary_constraint.add(total_salary <= 50000)

# Assign 9 players
model.one_position_constraint = ConstraintList()
for p in range(n_players):
    player_position_expr = sum(model.x[p, q] for q in range(n_positions))
    model.one_position_constraint.add(player_position_expr <= 1)

# Assign position as per index
model.position_constraint = ConstraintList()
for q in range(n_positions):
    position_player_expr = sum(model.x[p, q] for p in range(n_players) if pos_by_index[q] in players_df.loc[p, 'Pos'])
    model.position_constraint.add(position_player_expr == 1)

opt = SolverFactory('cbc')
opt_success = opt.solve(model, tee=True, timelimit=60)

model.pprint()




Welcome to the CBC MILP Solver 
Version: 2.10.8 
Build Date: Feb  3 2023 

command line - /content/bin/cbc -sec 60 -timeMode elapsed -printingOptions all -import /tmp/tmpkklh0mge.pyomo.lp -stat=1 -solve -solu /tmp/tmpkklh0mge.pyomo.soln (default strategy 1)
seconds was changed from 1e+100 to 60
Option for timeMode changed from cpu to elapsed
Option for printingOptions changed from normal to all
 CoinLpIO::readLp(): Maximization problem reformulated as minimization
Coin0009I Switching back to maximization to get correct duals etc
Presolve 422 (-37) rows, 2802 (-1239) columns and 6279 (-1276) elements
Statistics for presolved model
Original problem has 4041 integers (4041 of which binary)
Presolved problem has 2802 integers (2802 of which binary)
==== 534 zero objective 253 different
==== absolute objective values 253 different
==== for integers 534 zero objective 253 different
==== for integers absolute objective values 253 different
===== end objective counts


Problem has 422 rows, 28

In [31]:
# Printing results for the optimal allocation of 9 players
players_list1 = []
for q in range(n_positions):
    print("\nPosition", q, ":", pos_by_index[q])
    for p in range(n_players):
        if value(model.x[p, q]) > 0.5:
            print("\tPlayer", p, "\tName:", players_df.loc[p, 'Name'], "\tEV:", players_df.loc[p, 'SS Proj'],
                  "\tSalary:", players_df.loc[p, 'Salary'], "\tPosition:", players_df.loc[p, 'Pos'],
                  "\tTeam:", players_df.loc[p, 'Team'])
            players_list1.append(players_df.loc[p, 'Name'])

print("\nBest Expected Value:", value(objective_expr))


Position 0 : QB
	Player 5 	Name: Tom Brady 	EV: 22.7348 	Salary: 6600 	Position: QB 	Team: TB
	Player 9 	Name: Tony Pollard 	EV: 20.9832 	Salary: 5200 	Position: RB,FLEX 	Team: DAL
	Player 40 	Name: Emmanuel Sanders 	EV: 15.5059 	Salary: 4200 	Position: WR,FLEX 	Team: NO
	Player 64 	Name: Tre'Quan Smith 	EV: 11.9099 	Salary: 3200 	Position: WR,FLEX 	Team: NO

Position 1 : RB
	Player 255 	Name: Alexander Mattison 	EV: 0.0 	Salary: 6300 	Position: RB,FLEX 	Team: MIN

Position 2 : RB
	Player 303 	Name: Raymond Calais 	EV: 0.0 	Salary: 4000 	Position: RB,FLEX 	Team: LAR

Position 3 : WR
	Player 381 	Name: Dan Chisena 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: MIN

Position 4 : WR
	Player 356 	Name: Parris Campbell 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: IND

Position 5 : WR
	Player 0 	Name: Kyler Murray 	EV: 26.8949 	Salary: 7000 	Position: QB 	Team: ARI
	Player 347 	Name: Preston Williams 	EV: 0.0 	Salary: 3700 	Position: WR,FLEX 	Team: MIA

Position 6 : TE
	Player 441 	Na

In [32]:
# Extract the selected players' information
final_team = []
player_count = 0  # Initialize player count

for q in range(n_positions):
    for p in range(n_players):
        if model.x[p, q].value > 0.5:
            player_count += 1  # Increment player count
            player_info = {
                "Player": players_df['Name'][p],
                "EV": players_df['SS Proj'][p],
                "Salary": players_df['Salary'][p],
                "Position": players_df['Pos'][p],
                "Team": players_df['Team'][p],
                "PlayerNumber": player_count  # Assign player number
            }
            final_team.append(player_info)

# Print the final team 
print("Final Team:")
for player in final_team:
    print("Player Number:", player["PlayerNumber"])  # Print player number
    print("Player:", player["Player"])
    print("\tEV:", player["EV"])
    print("\tSalary:", player["Salary"])
    print("\tPosition:", player["Position"])
    print("\tTeam:", player["Team"])
    print()


Final Team:
Player Number: 1
Player: Tom Brady
	EV: 22.7348
	Salary: 6600
	Position: QB
	Team: TB

Player Number: 2
Player: Tony Pollard
	EV: 20.9832
	Salary: 5200
	Position: RB,FLEX
	Team: DAL

Player Number: 3
Player: Emmanuel Sanders
	EV: 15.5059
	Salary: 4200
	Position: WR,FLEX
	Team: NO

Player Number: 4
Player: Tre'Quan Smith
	EV: 11.9099
	Salary: 3200
	Position: WR,FLEX
	Team: NO

Player Number: 5
Player: Alexander Mattison
	EV: 0.0
	Salary: 6300
	Position: RB,FLEX
	Team: MIN

Player Number: 6
Player: Raymond Calais
	EV: 0.0
	Salary: 4000
	Position: RB,FLEX
	Team: LAR

Player Number: 7
Player: Dan Chisena
	EV: 0.0
	Salary: 3000
	Position: WR,FLEX
	Team: MIN

Player Number: 8
Player: Parris Campbell
	EV: 0.0
	Salary: 3000
	Position: WR,FLEX
	Team: IND

Player Number: 9
Player: Kyler Murray
	EV: 26.8949
	Salary: 7000
	Position: QB
	Team: ARI

Player Number: 10
Player: Preston Williams
	EV: 0.0
	Salary: 3700
	Position: WR,FLEX
	Team: MIA

Player Number: 11
Player: J.P. Holtz
	EV: 0

## PartB: Contraint 4: Stacking Constraint

In [33]:


model = ConcreteModel()
model.x = Var(range(n_players), range(n_positions), within=Binary)

## objective function
objective_expr = sum(
    model.x[p, q] * players_df['SS Proj'][p]
    for p in range(n_players)
    for q in range(n_positions)
    if players_df['SS Proj'][p] != 0
)

model.total_time = Objective(
    expr=objective_expr,
    sense=maximize
)


# Salary Constraint
model.salary_constraint = Constraint(
    expr=sum(
        model.x[p, q] * players_df['Salary'][p]
        for p in range(n_players)
        for q in range(n_positions)
        if players_df['SS Proj'][p] != 0
    ) <= 50000
)

# Assign 9 players
model.one_position_constraint = ConstraintList()
for p in range(n_players):
    model.one_position_constraint.add(
        sum(model.x[p, q] for q in range(n_positions)) <= 1
    )

# Assign position as per index
model.position_constraint = ConstraintList()
for q in range(n_positions):
    position_player_expr = sum(
        model.x[p, q] for p in range(n_players) if pos_by_index[q] in players_df['Pos'][p]
    )
    model.position_constraint.add(position_player_expr == 1)

# Stacking constraints
model.stacking_constraints = ConstraintList()
for p_dst in range(n_players):
    if players_df['Pos'][p_dst] != 'DST':
        continue
    opponent_team_name = players_df['Opp'][p_dst]
    for other_p in range(n_players):
        if players_df['Team'][other_p] == opponent_team_name:
            for q in range(n_positions):
                model.stacking_constraints.add(model.x[other_p, q] + model.x[p_dst, 7] <= 1)

for p_qb in range(n_players):
    if players_df['Pos'][p_qb] != 'QB':
        continue
    qb_team_name = players_df['Team'][p_qb]
    qb_receivers_expr = sum(
        model.x[other_p, q]
        for other_p in range(n_players)
        if players_df['Team'][other_p] == qb_team_name
        and ('TE' in players_df['Pos'][other_p] or 'WR' in players_df['Pos'][other_p])
        for q in range(n_positions)
    )
    model.stacking_constraints.add(2 * model.x[p_qb, 0] <= qb_receivers_expr)

opt = SolverFactory('cbc')
opt_success = opt.solve(model, tee=True, timelimit=60)

model.pprint()

# Printing results for the optimal allocation of 9 players with QB and DST constraints
players_list2 = []
for q in range(n_positions):
    print("\n", "Position", q, ":", pos_by_index[q])
    for p in range(n_players):
        if value(model.x[p, q] > 0.9):
            print("\tPlayer", p,
                  "\tName:", players_df['Name'][p],
                  "\tEV:", players_df['SS Proj'][p],
                  "\tSalary:", players_df['Salary'][p],
                  "\tPosition:", players_df['Pos'][p],
                  "\tTeam:", players_df['Team'][p])
            players_list2.append(players_df['Name'][p])
print("\n", "Best Expected Value for 9 players after stacking constraints:", value(objective_expr))


Streaming output truncated to the last 5000 lines.
        (129, 7) :     0 :   0.0 :     1 : False : False : Binary
        (129, 8) :     0 :   0.0 :     1 : False : False : Binary
        (130, 0) :     0 :   0.0 :     1 : False : False : Binary
        (130, 1) :     0 :   0.0 :     1 : False : False : Binary
        (130, 2) :     0 :   0.0 :     1 : False : False : Binary
        (130, 3) :     0 :   0.0 :     1 : False : False : Binary
        (130, 4) :     0 :   0.0 :     1 : False : False : Binary
        (130, 5) :     0 :   0.0 :     1 : False : False : Binary
        (130, 6) :     0 :   0.0 :     1 : False : False : Binary
        (130, 7) :     0 :   0.0 :     1 : False : False : Binary
        (130, 8) :     0 :   0.0 :     1 : False : False : Binary
        (131, 0) :     0 :   0.0 :     1 : False : False : Binary
        (131, 1) :     0 :   0.0 :     1 : False : False : Binary
        (131, 2) :     0 :   0.0 :     1 : False : False : Binary
        (131, 3) :     0 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



        2320 :  -Inf :                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [34]:
# Printing results for the optimal allocation of 9 players with QB and DST constraints
players_list2 = []
for q in range(n_positions):
    print("\n", "Position", q, ":", pos_by_index[q])
    for p in range(n_players):
        if model.x[p, q].value > 0.9:
            print("\tPlayer", p,
                  "\tName:", players_df['Name'][p],
                  "\tEV:", players_df['SS Proj'][p],
                  "\tSalary:", players_df['Salary'][p],
                  "\tPosition:", players_df['Pos'][p],
                  "\tTeam:", players_df['Team'][p])
            players_list2.append(players_df['Name'][p])
print("\n", "Best Expected Value for 9 players after stacking constraints:", value(objective_expr))


 Position 0 : QB
	Player 9 	Name: Tony Pollard 	EV: 20.9832 	Salary: 5200 	Position: RB,FLEX 	Team: DAL
	Player 272 	Name: C.J. Beathard 	EV: 0.0 	Salary: 5000 	Position: QB 	Team: SF
	Player 357 	Name: Lawrence Cager 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: NYJ
	Player 401 	Name: JJ Arcega-Whiteside 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: PHI

 Position 1 : RB
	Player 0 	Name: Kyler Murray 	EV: 26.8949 	Salary: 7000 	Position: QB 	Team: ARI
	Player 311 	Name: La'Mical Perine 	EV: 0.0 	Salary: 4000 	Position: RB,FLEX 	Team: NYJ
	Player 350 	Name: Quincy Adeboyejo 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: NE
	Player 366 	Name: John Franklin III 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: TB
	Player 369 	Name: Chris Moore 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: BAL
	Player 372 	Name: Bennie Fowler III 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: NO
	Player 387 	Name: Randall Cobb 	EV: 0.0 	Salary: 3000 	Position: WR,FLEX 	Team: HOU

 Position 2 

In [35]:


model = ConcreteModel()

# Initialize variables
model.x = Var(range(len(players_df)), range(n_positions), within=Binary)

# Objective function
model.total_time = Objective(
    expr=sum(model.x[p, q] * players_df.loc[p, 'SS Proj'] for p in range(len(players_df)) for q in range(n_positions)
             if players_df.loc[p, 'SS Proj'] != 0),
    sense=maximize
)

# Constraints
model.salary_constraint = Constraint(expr=sum(model.x[p, q] * players_df.loc[p, 'Salary']
                                              for p in range(len(players_df)) for q in range(n_positions)
                                              if players_df.loc[p, 'SS Proj'] != 0) <= 50000)

model.one_position_constraint = ConstraintList()
for p in range(len(players_df)):
    player_position_expr = sum(model.x[p, q] for q in range(n_positions))
    model.one_position_constraint.add(player_position_expr <= 1)

model.position_constraint = ConstraintList()
for q in range(n_positions):
    position_player_expr = sum(model.x[p, q] for p in range(len(players_df))
                               if pos_by_index[q] in players_df.loc[p, 'Pos'])
    model.position_constraint.add(position_player_expr == 1)

model.stacking_constraints = ConstraintList()
for p_dst in range(len(players_df)):
    if players_df.loc[p_dst, 'Pos'] != 'DST':
        continue
    opponent_team_name = players_df.loc[p_dst, 'Opp']
    for other_p in range(len(players_df)):
        if players_df.loc[other_p, 'Team'] == opponent_team_name:
            for q in range(n_positions):
                model.stacking_constraints.add(model.x[other_p, q] + model.x[p_dst, 7] <= 1)

for p_qb in range(len(players_df)):
    if players_df.loc[p_qb, 'Pos'] != 'QB':
        continue
    qb_team_name = players_df.loc[p_qb, 'Team']
    qb_receivers_expr = 0
    for other_p in range(len(players_df)):
        if players_df.loc[other_p, 'Team'] == qb_team_name:
            if 'TE' in players_df.loc[other_p, 'Pos'] or 'WR' in players_df.loc[other_p, 'Pos']:
                for q in range(n_positions):
                    qb_receivers_expr += model.x[other_p, q]
    model.stacking_constraints.add(2 * model.x[p_qb, 0] <= qb_receivers_expr)

# Solve the optimization problem
opt = SolverFactory('cbc')
opt_success = opt.solve(model, tee=True, timelimit=60)

#


Welcome to the CBC MILP Solver 
Version: 2.10.8 
Build Date: Feb  3 2023 

command line - /content/bin/cbc -sec 60 -timeMode elapsed -printingOptions all -import /tmp/tmp3r82beqh.pyomo.lp -stat=1 -solve -solu /tmp/tmp3r82beqh.pyomo.soln (default strategy 1)
seconds was changed from 1e+100 to 60
Option for timeMode changed from cpu to elapsed
Option for printingOptions changed from normal to all
 CoinLpIO::readLp(): Maximization problem reformulated as minimization
Coin0009I Switching back to maximization to get correct duals etc
Presolve 3922 (-638) rows, 3451 (-590) columns and 20150 (-1829) elements
Statistics for presolved model
Original problem has 4041 integers (4041 of which binary)
Presolved problem has 3451 integers (3451 of which binary)
==== 1183 zero objective 253 different
==== absolute objective values 253 different
==== for integers 1183 zero objective 253 different
==== for integers absolute objective values 253 different
===== end objective counts


Problem has 3922 row

In [36]:
#Printing results for the optimal allocation of 9 players with QB and DST constraints
players_list2 = []
for q in range(n_positions):
  print("\n","Position ", q, ": ", pos_by_index[q])
  for p in range(n_players):
    if value(model.x[p,q] > 0.9):
      print("\tPlayer ", p, 
            "\tName: ", players_df['Name'][p],
            "\tEV:",  players_df['SS Proj'][p], 
            "\tSalary: ", players_df['Salary'][p], "\t", 
            "\tPosition: ", players_df['Pos'][p], "\t",
            "\tTeam: ", players_df['Team'][p])
      players_list2.append(players_df['Name'][p])



 Position  0 :  QB
	Player  9 	Name:  Tony Pollard 	EV: 20.9832 	Salary:  5200 	 	Position:  RB,FLEX 	 	Team:  DAL
	Player  272 	Name:  C.J. Beathard 	EV: 0.0 	Salary:  5000 	 	Position:  QB 	 	Team:  SF
	Player  357 	Name:  Lawrence Cager 	EV: 0.0 	Salary:  3000 	 	Position:  WR,FLEX 	 	Team:  NYJ
	Player  401 	Name:  JJ Arcega-Whiteside 	EV: 0.0 	Salary:  3000 	 	Position:  WR,FLEX 	 	Team:  PHI

 Position  1 :  RB
	Player  0 	Name:  Kyler Murray 	EV: 26.8949 	Salary:  7000 	 	Position:  QB 	 	Team:  ARI
	Player  311 	Name:  La'Mical Perine 	EV: 0.0 	Salary:  4000 	 	Position:  RB,FLEX 	 	Team:  NYJ
	Player  350 	Name:  Quincy Adeboyejo 	EV: 0.0 	Salary:  3000 	 	Position:  WR,FLEX 	 	Team:  NE
	Player  366 	Name:  John Franklin III 	EV: 0.0 	Salary:  3000 	 	Position:  WR,FLEX 	 	Team:  TB
	Player  369 	Name:  Chris Moore 	EV: 0.0 	Salary:  3000 	 	Position:  WR,FLEX 	 	Team:  BAL
	Player  372 	Name:  Bennie Fowler III 	EV: 0.0 	Salary:  3000 	 	Position:  WR,FLEX 	 	Team:  NO
	Pla